#Preliminary Code

## Mount Google Drive Data

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


First, I am going to work with just trying to get a k-mer coutning program working. Thus, I will start small with one sequence of length 100. Then I will move on to multiple sequences of length 100 to replicate using contigs as opposed to an assembled genome. Eventually, once I get the k-mer counting working, I will move on to trying to utilize the k-mer counts in machine learning algorithms.

## Import Packages

In [ ]:
#Import packages
from datetime import datetime, date
import random
from operator import itemgetter
from sklearn.model_selection import train_test_split, KFold
from sklearn import svm
import sys
import numpy as np

## Create Random Sequence

In [ ]:
# def generate_rand_sequence(length):
#   sequence = "" #Initialize sequence
#   for i in range(0,length):
#     check = random.randint(1,4)
#     if check == 1: sequence += "A"
#     elif check == 2: sequence += "T"
#     elif check == 3: sequence += "C"
#     else: sequence += "G"
#   return(sequence)

Saving first sequence created in its own variable so it will not change with each run.

In [ ]:
# c_sequence = "ACGTAGGCGACCGCCGGCAAAGGTACGGATTCTTTATGACAAGAAAGTATGACGAGTTGAGGACCTGATGGGAGCAAGAGGTCGTTCCTCTGGCGGTTCG"

# Naive Approach to k-mer Counting
This will count k-mers in the simplest way possible. It will iterate through a list checking to see if a k-mer has been seen before. If it has, it increases the count for that k-mer, if it hasn't, it adds it to the list.

##Gets the kmer count in an array using the naive approach

In [ ]:
#functions

##returns the smaller alphabetically of the forward and reverse complement
def get_alph_comp(forward):
  rev_comp = ""
  for n in range(len(forward),0,-1):
    if forward[n-1:n]=="A": rev_comp += "T"
    elif forward[n-1:n]=="T": rev_comp += "A"
    elif forward[n-1:n]=="C": rev_comp += "G"
    else: rev_comp += "C"
  for n in range(0,len(forward)):
    if forward[n:n+1] < rev_comp[n:n+1]:
      return forward
    elif forward[n:n+1] > rev_comp[n:n+1]:
      return rev_comp
  return rev_comp


#Gets k-mer count given a k value using a naive vector indexed search approach
def naive_count(k, seq, kmer_count):
  for i in range(0,len(seq)-(k-1)):
    check = seq[i:i+k]
    check = get_alph_comp(check)
    check_val = 0
    for j in range(0,len(kmer_count)):
      if check == kmer_count[j][0]:
        kmer_count[j][1] += 1
        check_val=1
        break
    if check_val==0:
      kmer_count.append([check,1])

  return(kmer_count)



Testing to make sure things are working.

In [ ]:
# print(naive_count(5,c_sequence))
# print(naive_count(10,c_sequence))
# print(naive_count(1,c_sequence))

In [ ]:
# test = generate_rand_sequence(1000)
# naive_count(31,test)

# Implementing Hash Tables (Dictionaries)
I have done some reading on hash tables and how they work. I am going to now attempt to implement a basic python dictionary to see how it performs with the same data.

##Gets the dictionary of kmers from a sequence

In [ ]:
#Gets k-mer count given a k value using a dictionary
def dictionary_count(k, seq, kmer_dict):
  for i in range(0,len(seq)-(k-1)):
    check = seq[i:i+k]
    check = get_alph_comp(check)
    if check in kmer_dict: kmer_dict[check] += 1
    else: kmer_dict[check] = 1
  return(kmer_dict)


Comparing how the naive approach and the dictionary approach perform at various differen sequence lengths.

In [ ]:
# t_1k = generate_rand_sequence(1000)
# t_10k = generate_rand_sequence(10000)
# t_100k = generate_rand_sequence(100000)
# t_1m = generate_rand_sequence(1000000)

# n_t_1k = []
# d_t_1k = {}
# n_t_10k = []
# d_t_10k = {}
# n_t_100k = []
# d_t_100k = {}
# d_t_1m = {}

# print("1,000")
# start = datetime.now().time()
# n_t_1k = naive_count(31, t_1k, n_t_1k)
# end = datetime.now().time()
# print("Compute time for Naive: ", datetime.combine(date.min, end)-datetime.combine(date.min, start))
# start_time = datetime.now().time()
# d_t_1k = dictionary_count(31, t_1k, d_t_1k)
# end = datetime.now().time()
# print("Compute time for Dictionary: ", datetime.combine(date.min, end)-datetime.combine(date.min, start))

# print("10,000")
# start = datetime.now().time()
# n_t_10k = naive_count(31, t_10k, n_t_10k)
# end = datetime.now().time()
# print("Compute time for Naive: ", datetime.combine(date.min, end)-datetime.combine(date.min, start))
# start = datetime.now().time()
# d_t_10k = dictionary_count(31, t_10k, d_t_10k)
# end = datetime.now().time()
# print("Compute time for Dictionary: ", datetime.combine(date.min, end)-datetime.combine(date.min, start))


# print("100,000")
# start = datetime.now().time()
# n_t_100k = naive_count(31, t_100k, n_t_100k)
# end = datetime.now().time()
# print("Compute time for Naive: ", datetime.combine(date.min, end)-datetime.combine(date.min, start))
# start = datetime.now().time()
# d_t_100k = dictionary_count(31, t_100k, d_t_100k)
# end = datetime.now().time()
# print("Compute time for Dictionary: ", datetime.combine(date.min, end)-datetime.combine(date.min, start))

# print("1,000,000")
# #start = datetime.now().time()
# #n_t_1m = naive_count(31,t_1m)
# #end = datetime.now().time()
# #print("Compute time for Naive: ", datetime.combine(date.min, end)-datetime.combine(date.min, start))
# start = datetime.now().time()
# d_t_1m = dictionary_count(31, t_1m, d_t_1m)
# end = datetime.now().time()
# print("Compute time for Dictionary: ", datetime.combine(date.min, end)-datetime.combine(date.min, start))


This next section of code was used to verfiy that both functions were running as intended and providing the same output.

In [ ]:
# sublist = n_t_1k[85:95]
# print(sublist)

In [ ]:
# keylist = []
# for item in sublist:
#   keylist.append(item[0])
# print(keylist)
# type(keylist[0])
# for x in keylist:
#   print(d_t_1k.get(x))

# Running Code on Real Data
This next section will focus on trying to get the code to work on a real FASTA file that comes from the dataset I am trying to work with. Some small adjustments to the code need to be done so that I can read in sequences from the file one at a time as not to overload the memory.

##Gets the dictionary of kmers from a file

In [ ]:
def kmer_count(k, file):
  kmer_dict = {}
  with open(file) as seq_file:
  #Initializing variables needed for loops
    remainder = ""
    #Loop through lines of file
    for line in seq_file:
      #Check to see if we are starting a new sequence
      if line[0] == '>':
        remainder = "" #Clear the remainder as the next sequence is not related to previous
      #This means the line contains sequencing data
      else:
        line = remainder + line #Add the remainder from the previous line in the sequence
        kmer_dict = dictionary_count(k,line,kmer_dict) #update the dictionary
        remainder = line[-(k-1)+1:-1] #Update the remainder with last k-1 characters of the line (the +1 is to avoid new line character)
  return(kmer_dict)

In [ ]:

# #skip #40 and 92 as the files are not included for some reason

# for i in range(36,96):
#   if i == 40 or i == 92:
#     continue
#   filename = "SRR87375" + str(i) + "_scaffolds.fasta"
#   filepath = '/content/drive/MyDrive/AMR/Data/Scaffold_fasta/' + filename
#   savefile = '/content/drive/MyDrive/AMR/Data/Scaffold_kmers/SRR87375' + str(i) + '_kmers.npy'
#   start = datetime.now().time()
#   kmer_dict = kmer_count(31,filepath)
#   end = datetime.now().time()
#   np.save(savefile,kmer_dict)
#   print("Compute time for ",filename ,": ", datetime.combine(date.min, end)-datetime.combine(date.min, start))


Now that we can count k-mer on an entire set of files, we can begin testing mahine learning algorithms on these datasets. One test I would like to run is seeing if using the count data, as opposed to a binary presence/absence, would increase the accuracy of AMR prediction when using SCM. Additionally, Dr. Drouin talks about using unitigs as opossed to kmers due to the redundancy of k-mers amongst individual genome sequences.

Dr. Bailey was wondering whether or not a different length k-mer would matter when dealing with count data as opposed to binary presence/abscence data for each k-mer.

Also, want to compare classification tree to SCM to see advantages/disadvantages of each. Thea reason for this is these two models are both often seen as interpretable.

# Converting dictionaries files to absence/presence vector

I need to create another version of dictionary_count that takes in these numpy files and creates one large dictionary for all the kmers present in the entire dataset.

##Compiles all .npy dictionaries into a single .npy dictionary for the entire dataset

In [ ]:
# #Gets k-mer count given a k value using a dictionary
# def pres_abs_cumm(pres_abs_dict, kmer_dict):
#   for key in kmer_dict:
#     if key not in pres_abs_dict: pres_abs_dict[key] = 1
#   return(pres_abs_dict)

# cumm_pres_abs_dict = {}
# for i in range(36,96):
#   if i == 40 or i == 92:
#     continue
#   filepath = '/content/drive/MyDrive/AMR/Data/Scaffold_kmers/SRR87375' + str(i) + '_kmers.npy'
#   individual_file_dict = np.load(filepath,allow_pickle='TRUE').item()
#   cumm_pres_abs_dict = pres_abs_cumm(cumm_pres_abs_dict, individual_file_dict)
# savefile = '/content/drive/MyDrive/AMR/Data/global_vals/pres_abs__scaff_dict.npy'
# np.save(savefile,cumm_pres_abs_dict)

Now I need to convert the pres/abs dictionary into a vector that can has an index notation. I should be able to take advantage of the fact that I have a dictionary for each individual sample. I can use this to look up the value in each sample quickly and then assign it to the vector. I plan on making both a pres/abs vector, as well as a count vector in the hopes that I will be able to mess around with the count vector a little more in the future.

##Creates a vector of the kmers from the entire dataset dictionary

In [ ]:
# filepath = '/content/drive/MyDrive/AMR/Data/global_vals/pres_abs__scaff_dict.npy'
# temp_dict = np.load(filepath,allow_pickle='TRUE').item()
# size = len(temp_dict)
# key_vector = np.empty(size,dtype=object)
# count=0
# for item in temp_dict:
#   key_vector[count] = item
#   count+= 1
# savepath = '/content/drive/MyDrive/AMR/Data/global_vals/key_vector.npy'
# np.save(savepath, key_vector)

##Creates the presence/absence vector for each individual dictionary using that dictionary and the key vector

In [ ]:

# for i in range(36,96):
#   zero_vector = np.zeros(size,dtype=int)
#   if i == 40 or i == 92:
#     continue
#   filename = '/content/drive/MyDrive/AMR/Data/Scaffold_kmers/SRR87375' + str(i) + '_kmers.npy'
#   file_dict = np.load(filename,allow_pickle='TRUE').item()
#   count = 0
#   for j in key_vector:
#     if j in file_dict: zero_vector[count]=1 
#     count += 1
#   savename = '/content/drive/MyDrive/AMR/Data/Scaffold_Presence/SRR87375' + str(i) + '_presence.npy'
#   np.save(savename,zero_vector)

##Testing to make sure the presence/absence vectors appear correct

In [ ]:
# filename2 = '/content/drive/MyDrive/AMR/Data/global_vals/key_vector.npy'
# key_vector = np.load(filename2,allow_pickle='TRUE')

##Testing cont.

In [ ]:
# filename = '/content/drive/MyDrive/AMR/Data/Scaffold_Presence/SRR8737550_presence.npy'
# file_vector = np.load(filename,allow_pickle='TRUE')

# print(file_vector[100:1000])

#Machine Learning Algorithms

First, need to create a label vector for each resistance type that tells whether the individual sample is resistant or not

##Function: Creates label vector

In [ ]:
def get_label_vector(resistance, matrix):
  column = 0
  for i in matrix[0,:]:
    if resistance == i:
      break
    column += 1
    if column == matrix[0,:].size:
      sys.exit("Resistance type not applicable")
  submatrix = matrix[:,[0,column]]
  delete_rows = []
  for i in range(0,submatrix[:,1].size):
    if submatrix[i,1] =='-':
      delete_rows.append(i)
  submatrix = np.delete(submatrix,delete_rows,0)
  return submatrix

##Creating the label vectors


In [ ]:
labels_csv = "/content/drive/MyDrive/AMR/Data/global_vals/Pseudomonas_Resistance_Labels.csv"
labels_matrix = np.genfromtxt(labels_csv,delimiter=',',dtype=str)
Tobra = get_label_vector('Tobramycin',labels_matrix)
Cefta = get_label_vector('Ceftazidim',labels_matrix)
Cipro = get_label_vector('Ciprofloxacin',labels_matrix)
Mero = get_label_vector('Meropenem',labels_matrix)
Coli = get_label_vector('Colistin',labels_matrix)

##SVM

In [ ]:
resist = Tobra
sample_num = resist[1:,0].size

##Used to obtain number of features
# file_path = "/content/drive/MyDrive/AMR/Data/Scaffold_Presence/SRR8737536_presence.npy"
# sample = np.load(file_path,allow_pickle='TRUE')
# sample.size

feat_num = 28522323   #28.5 million

X = np.empty(shape=(sample_num,feat_num),dtype=str)
for i in range(1, sample_num+1):
  file_path = "/content/drive/MyDrive/AMR/Data/Scaffold_Presence/" + resist[i,0] + "_presence.npy"
  sample = np.load(file_path,allow_pickle='TRUE')
  X[i-1,:] = sample


In [ ]:
X_train, X_test, y_train, y_test = train_test_split(
    X, resist[1:,1], test_size=0.2, random_state=0)
kf = KFold(n_splits = 5)
for train_index, test_index in kf.split(X):
  print("Train: ", train_index," Test: ", test_index)

# >>> X_train.shape, y_train.shape
# ((90, 4), (90,))
# >>> X_test.shape, y_test.shape
# ((60, 4), (60,))

# >>> clf = svm.SVC(kernel='linear', C=1).fit(X_train, y_train)
# >>> clf.score(X_test, y_test)